# Categorización de la Oferta Pública mediante ténicas Big Data
## Intro (la prepararemos para la defensa)

Carga de módulos y funciones necesarias

In [2]:
from helpers import get_db_connection, construct_dupes_dict
from config import MALLET_BINARY_PATH
from gensim import corpora
from gensim.test.utils import datapath
from gensim.models.wrappers import ldamallet
from gensim.models.wrappers import LdaMallet
from vocabulary_generator.text_cleaner import remove_accents, remove_irrelevant_tokens, apply_equivalences
import pyLDAvis.gensim as gensimvis
import pyLDAvis
from topic_modeler.model_generator import load_model, train_model, save_model 

Este notebook dispone de diversos modelos de tópicos previamente entrenados en el directorio _models_. El nombre de los ficheros contenidos en este directorio siguen la estructura **model_{docs}_{topics}**, donde **{docs}** representa el número de documentos utilizado y **{topics}** representa el número de tópicos de los que consta el modelo. La siguiente instrucción muestra los modelos pre-entrenados disponibles:

In [7]:
!ls models

model_2344_20


Para cargar el modelo elegido:

In [ ]:
lda_model = load_model('model_2344_20')

Para generar un nuevo modelo:

In [3]:
db_conn = get_db_connection()

num_topics = 400


df = db_conn.readDBtable(tablename='texts')

doc_urls = df['doc_url'].tolist()
tokens = df['tokens'].tolist()
doc_dupes_dict = construct_dupes_dict(doc_urls)
# print(doc_dupes_dict)
documents = list()
for doc in doc_dupes_dict:
    indices = doc_dupes_dict[doc]
    token_lists = [remove_accents(tokens[index]).split() for index in indices]
    doc_tokens = [token for token_list in token_lists for token in token_list]
    doc_tokens = apply_equivalences(remove_irrelevant_tokens(doc_tokens))
    documents.append(doc_tokens)

dictionary = corpora.Dictionary(documents)
max_tokens = len(dictionary.keys())
print(f'Num tokens before cleanup {len(dictionary.keys())}')
dictionary.filter_extremes(no_below=10, no_above=0.5, keep_n=max_tokens)
print(f'Num tokens after cleanup {len(dictionary.keys())}')
corpus_bow = [dictionary.doc2bow(doc) for doc in documents]
mallet_model = LdaMallet(mallet_path=MALLET_BINARY_PATH, corpus=corpus_bow, id2word=dictionary, num_topics=num_topics)
lda_model = ldamallet.malletmodel2ldamodel(mallet_model)

MySQL database connection successful
Num tokens before cleanup 50588
Num tokens after cleanup 7945


In [ ]:
'protection' in dictionary.itervalues()

In [4]:
vis_data = gensimvis.prepare(lda_model, corpus_bow, dictionary)
pyLDAvis.display(vis_data)

/home/ohm/Documentos/TFG/venv/lib/python3.7/site-packages/pyLDAvis/_prepare.py:223: RuntimeWarning: divide by zero encountered in log
  kernel = (topic_given_term * np.log((topic_given_term.T / topic_proportion).T))
/home/ohm/Documentos/TFG/venv/lib/python3.7/site-packages/pyLDAvis/_prepare.py:240: RuntimeWarning: divide by zero encountered in log
  log_lift = np.log(topic_term_dists / term_proportion)
/home/ohm/Documentos/TFG/venv/lib/python3.7/site-packages/pyLDAvis/_prepare.py:241: RuntimeWarning: divide by zero encountered in log
  log_ttd = np.log(topic_term_dists)
/home/ohm/Documentos/TFG/venv/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))
